In [43]:
import numpy as np
import matplotlib.pyplot as plt
from numba import jit
% matplotlib inline
import bokeh.plotting as blt
import bokeh
bokeh.io.output_notebook()

Loading BokehJS ...

In [162]:
#ecc=0.5
M=1
m=0.9
t=500

nPsi=360
nRad=400
minRad=1
maxRad=100
minPsi=0 #in multiples of pi
maxPsi=2

psis=np.pi*(minPsi+(maxPsi-minPsi)*np.arange(nPsi)/nPsi)+1e-6
psi=np.tile(psis.T,(nRad,1)).T
rads=minRad+(maxRad-minRad)*np.arange(nRad)/nRad
rad=np.tile(rads,(nPsi,1))

eccs=0.15+np.arange(4)*0.2
figs=[]
cmap = bokeh.models.LinearColorMapper(palette="PuOr11", low=0.5, high=2)

for ecc in eccs:
    a=findA(rad,psi)
    newRads=findRad(rad,psi,t)
    
    fig=blt.figure(x_range=[minRad,maxRad],y_range=[minPsi,maxPsi],x_axis_label='r(t=0) [arbitrary units]',y_axis_label='\u03D5(t=0) [units of \u03C0]',
                   title='r(t='+str(t)+') for e = '+str(ecc),plot_height=250)
    fig.image(image=[newRads/rad],x=minRad,y=minPsi,dw=(maxRad-minRad),dh=(maxPsi-minPsi), color_mapper=cmap)

    cbar = bokeh.models.ColorBar(color_mapper=cmap, border_line_color=None, location=(0,0),title='r(t)/r(0)')
    fig.add_layout(cbar, 'right')
    
    figs.append(fig)

grid=bokeh.layouts.gridplot(figs[:],ncols=1)
    
blt.show(grid)

In [160]:
def findEps(a,alpha):
    return np.sqrt(1-(M/m)*(a*(1-ecc**2))/alpha)
def findAlpha(rad,psi):
    a=findA(rad,psi)
    return (m/M)*((1/a)-2*(1-(m/M))/rad)**-1
def findPhi0(eps,psi):
    phi0=psi - np.arccos((1/eps) * (M*(1+ecc*np.cos(psi))/m - 1))
    phi0[np.sin(psi)*np.sin(psi-phi0)<0]+=np.pi
    return phi0
def findA(rad,psi):
    return rad*(1+ecc*np.cos(psi))/(1-ecc**2)
def findRad(rad,psi,t):
    a=findA(rad,psi)
    alpha=findAlpha(rad,psi)
    eps=findEps(a,alpha)
    phi0=findPhi0(eps,psi)
    phi=findPhi(eps,alpha,phi0,psi,t)
    #phi=(psi+t*np.sqrt(m/alpha**3)) % (2*np.pi) #this is a really stupid approximation
    #print('number of orbits: ',t*np.sqrt(m/alpha**3))
    #print('diff phi ',psi-phiDash)
    return alpha*(1-eps**2)/(1+eps*np.cos(phi+phi0))
def findPhi(eps,alpha,phi0,psi,t):
    #print('eps ',eps)
    #print('alpha ',alpha)
    #print('phi0 ',phi0%2*np.pi)
    #print('psi ',psi)
    #print('t ',t)
    import scipy.optimize
    def t_eta(eta,eps,alpha,t): #0 for eta=eta(t)
        return t-np.sqrt(alpha**3/(m))*(eta+eps*np.sin(eta))
    eta0=2*np.arctan(np.sqrt((1-eps)/(1+eps))*np.tan((psi-phi0)/2)) % (2*np.pi)
    #print('eta0 ',eta0)
    t0=-np.sqrt(alpha**3/(m))*(eta0+eps*np.sin(eta0)) #time (relative to pericenter passage) of mass drop
    #t0[t0<0]+=2*np.pi*np.sqrt(alpha[t0<0]**3/m)
    #print('t0 ',t0)
    #print('periods ',2*np.pi*np.sqrt(alpha**3/(m)))
    tDash=(t-t0) % (2*np.pi*np.sqrt(alpha**3/(m)))
    #print('tDash ',tDash)
    
    #can't vectorise optimization?
    phi=np.zeros_like(phi0)
    for (i,j),val in np.ndenumerate(phi):
        #print('i,j ',i,j)
        #print('vars: ',eps[i,j],alpha[i,j],tDash[i,j])
        eta=scipy.optimize.brentq(t_eta,0,2*np.pi,args=(eps[i,j],alpha[i,j],tDash[i,j])) #finds eta for the current time (between 0 and 2*pi)
        #print('eta: ',eta)
        phi[i,j]=phi0[i,j]+2*np.arctan(np.sqrt((1+eps[i,j])/(1-eps[i,j]))*np.tan(eta/2))
    
    #attempt to vectorize, reshapes etaGuess to be 1d and doesn't work. Prolly v fixable...
    #etaGuess=(np.pi)*np.ones_like(phi0)
    #eta=scipy.optimize.root(t_eta,etaGuess[:],args=(eps[:],alpha[:],tDash[:]))
    #phi=phi0+2*np.arctan(np.sqrt((1+eps)/(1-eps))*np.tan(eta/2))
    
    #print('fraction of orbit ',(tDash)/(2*np.pi*np.sqrt(alpha**3/(m))))
    #print('phi ',phi)
    return phi

In [161]:
fig=blt.figure()
fig.line(rad[0,:],newRads[0,:],line_width=10)
blt.show(fig)

In [ ]:
#from old code
import scipy.optimize
def findEtas(R): #finds etas for which r(eta)=R
    value,lowInt = min((b,a) for a,b in enumerate(turn-etaMin(R)) if (b>0 and a%2==1))
    lowInt-=1
    if (findRad(turn[lowInt+1])-R>0):
        lowInt+=2
    value,highInt = min((b,a) for a,b in enumerate(turn-etaMax(R)) if (b>0 and a%2==0))
    highInt-=1
    if (R-findRad(turn[highInt-1])>0):
        highInt-=2
    nInt=highInt-lowInt
    etas=np.zeros(nInt)
    diff=0
    for i in range(0,nInt):
        if (i==0):
            if (findRad(turn[lowInt])<R):
                etas=etas[:-1]
                diff=-1
                continue
        if (i==nInt-1):
            if (findRad(turn[highInt])<R and findRad(turn[highInt-1])<R):
                etas=etas[:-1]
                break
        lowerBound=turn[lowInt+i+diff]
        upperBound=turn[lowInt+i+1+diff]
        etas[i+diff]=scipy.optimize.brentq(F,lowerBound,upperBound,args=(R))
    return etas